# AI Fantasy Hockey Player 

This project will create an AI Hockey player in a fantasy league. 

In [5]:
from dotenv import load_dotenv
from yahoo_oauth import OAuth2
import yahoo_fantasy_api as yfa
import os
import requests
from rapidfuzz import fuzz
from openai import OpenAI
import pandas as pd

from scraper import fetch_website_contents
from IPython.display import Markdown, display
import ollama
import json

# from week1.day1 import system_prompt

load_dotenv()

# system_prompt = """
# You are a professional hockey analyst and an experienced fantasy hockey owner.
# Your task is to analyze a list of NHL free agent players along with their complete statistics.
# Your goal is to select the **top 3 players for each position** (C, LW, RW, G, D) that a fantasy manager should pick up.

# - Consider all available stats: goals, assists, points, hits, blocked shots, plus-minus, shots, penalty minutes, and any other relevant metrics.
# - Prioritize players who maximize fantasy points and contribute most to team performance.
# - Provide a brief justification for each selected player.
# - Respond in **markdown** only, structured in clear tables or bullet points.
# - **Do NOT wrap the markdown in a code block.**
# - Focus on actionable fantasy advice, not general NHL commentary.
# """
# user_prompt_prefix = """
# Here is the full dataset of available free agent players with their statistics:

# {player_stats}

# Based on this data:
# 1. Identify the **top 3 players per position**.
# 2. Provide a **summary table** with player name, position, team, and key stats.
# 3. Include a **brief justification** for why each player is recommended.
# 4. Format everything in **readable markdown** for quick fantasy decision-making.

# Provide the output only as markdown.
# """


# You should respond in JSON as in this example for these 3 positions positions = ["C", "LW", "RW", "G"]  

# {
#     "positionType": [
#         {"playerName": "John Smith", "team": "VGK", ...include other stats},
#     ]
# }

system_prompt = f"""
You are provided with a list of data for different free agent players in the NHL.

Your task:
- Analyze the player data and decide which players would be most valuable to include in a fantasy hockey team based on their statistics.
- Use the player data grouped by position types: positions = ["C", "LW", "RW", "G"].
- Instead of showing any Python code, display the **final output** directly as formatted tables.

Each table should:
- Have a clear title, e.g., "🏒 Player Stats by Position Type – Centers (C)".
- Display rows of player statistics with columns such as:
  playerName | team | gamesPlayed | goals | assists | points | plusMinus | penaltyMinutes
- For goalies ("G"), use columns like:
  playerName | team | gamesPlayed | wins | losses | savePct | GAA | shutouts
- Format the tables neatly with headers and borders similar to how pandas DataFrames appear in notebooks.

Example Output:

### 🏒 Player Stats by Position Type – Centers (C)

| playerName   | team | gamesPlayed | goals | assists | points | plusMinus | penaltyMinutes |
|---------------|------|--------------|--------|----------|----------|------------|----------------|
| John Smith    | VGK  | 82           | 30     | 45       | 75       | +12        | 20             |
| Eddy Bright   | NYR  | 80           | 28     | 50       | 78       | +15        | 10             |

### 🥅 Player Stats by Position Type – Goalies (G)

| playerName   | team | gamesPlayed | wins | losses | savePct | GAA | shutouts |
|---------------|------|--------------|-------|----------|----------|------|-----------|
| Carter Green  | BOS  | 62           | 38    | 17       | .917     | 2.41 | 5         |

Only show the tables as the final response — do not include Python code, setup, or explanations.
"""



user_prompt=f"""Here is the full dataset of available free agent players with their statistics. Based on the Data, identify top 3 players for each position. Provide a **summary table** with player name, position, team, and key stats.
# 3. Include a **brief justification** for why each player is recommended.
# 4. Format everything in **readable json** for quick fantasy decision-making."""


load_dotenv(override=True)
CLIENT_ID = os.getenv("YAHOO_CLIENT_ID")
CLIENT_SECRET = os.getenv("YAHOO_CLIENT_SECRET")

if not CLIENT_ID or not CLIENT_SECRET:
    raise EnvironmentError("Missing YAHOO_CLIENT_ID or YAHOO_CLIENT_SECRET in .env file")


TOKEN_FILE = "oauth2.json"
if os.path.exists(TOKEN_FILE):
    sc = OAuth2(None, None, from_file=TOKEN_FILE)
else:
    sc = OAuth2(CLIENT_ID, CLIENT_SECRET)  # Opens browser for first login
    print(f"✅ OAuth approved. Token saved automatically to {TOKEN_FILE}")


game = yfa.Game(sc, "nhl")  # "nhl" = hockey


leagues = game.league_ids(year=2025)
if not leagues:
    raise ValueError("No Yahoo Fantasy Hockey leagues found for this account")
print(leagues)
league_id = '465.l.38109'
league = game.to_league(league_id)
print(league)

print("📊 Standings:")
for team in league.standings():
    print(team["name"])



def get_healthy_free_agents(position):
    free_agents = league.free_agents(position)  # get all players at this position
    healthy = [p for p in free_agents if p.get("status") == "" and p.get("teamAbbrev") != ""]  # filter only free agents
    return healthy

positions = ["C", "LW", "RW", "G"]  # example positions
all_free_agents = []
for pos in positions:
    all_free_agents.extend(get_healthy_free_agents(pos))

print(f"Found {len(all_free_agents)} healthy free agents.\n")


nhl_url = "https://api.nhle.com/stats/rest/en/skater/realtime"
params = {
    "limit": -1,
    "cayenneExp": "seasonId=20252026 and gameTypeId=2"
}

response = requests.get(nhl_url, params=params)
nhl_stats = response.json()["data"]

if response.status_code != 200:
    raise ConnectionError(f"NHL API request failed with status {response.status_code}")



matched_players = []

for player in all_free_agents:
    y_name = player["name"].lower()
    best_match = None
    best_score = 0
    
    for s in nhl_stats:
        nhl_name = s.get("skaterFullName", "").lower()
        score = fuzz.ratio(y_name, nhl_name)  # fuzzy matching
        
        if score > best_score:
            best_score = score
            best_match = s

        print("best_score", best_score)
    if best_score >=90:
        player_stats = best_match.copy()
        player_stats["yahoo_name"] = player["name"]
        player_stats["position_type"] = player["position_type"]
        matched_players.append(player_stats)
    # else:
    #     matched_players.append({
    #         "yahoo_name": player["name"],
    #         "position_type": player["position_type"]
    #     })


print(f"📊 {len(matched_players)} Available Free Agents with NHL Stats:\n")

print(matched_players)
def messages_for(content):
    return [
        {"role": "system", "content": system_prompt},
        {"role": "user", "content": user_prompt + content},
    ]



def summarize(model, use_openai=False):
    content = json.dumps(matched_players, indent=2)
    messages = messages_for(content)  

    if use_openai == True:
        client = OpenAI()
        response = client.chat.completions.create(
            model="gpt-5-nano",
            messages=messages
        )
        return response.choices[0].message.content
    else:
        response = ollama.chat(model=model, messages=messages)
        return response["message"]["content"]


def display_summary(model="llama3.2",use_openai=False ):
    summary = summarize(model, use_openai)
    print("\nUsing Model", model,"\n")
    display(Markdown(summary))

display_summary("llama3.2", use_openai=False)
display_summary("gpt-4.1-nano", use_openai=True)






[2025-10-24 08:55:36,239 DEBUG] [yahoo_oauth.oauth.handler] AUTHORIZATION URL : https://api.login.yahoo.com/oauth2/request_auth?redirect_uri=oob&response_type=code&client_id=dj0yJmk9czNGVUtHMGozNFg2JmQ9WVdrOVdVdHlkM3BSTjNVbWNHbzlNQT09JnM9Y29uc3VtZXJzZWNyZXQmc3Y9MCZ4PWVk


✅ OAuth approved. Token saved automatically to oauth2.json
['465.l.38109']
📊 Standings:
Arrest Guenther Glidin'
Ottawa League Prisoner
$17 Million Dollar Man
Papis Mustache Ride
Globo Gym Cobras
North Kariya
Meet the Faulkers
Da Vinki
Buium Goes the Dynamite
Grant's Genius Team
Honey Badgers
Vezina Champs
Found 424 healthy free agents.

best_score 34.78260869565217
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.84615384615385
best_score 53.846153846

It looks like you've provided a JSON array of player data, but I'll assume it's in a format that can be easily parsed and analyzed.

Based on the data, I can tell you some basic statistics about each player. Here are the results:

**Top 5 Players by Blocked Shots**

1. Beckett Sennecke (ANA) - 9 blocked shots
2. Michael Brandsegg-Nygård (DET) - 12 blocked shots
3. Collin Graf (SJS) - 11 blocked shots
4. David Tomasek (EDM) - 10 blocked shots
5. Maxim Tsyplakov (NYI) - 9 blocked shots

**Top 5 Players by Shots Blocked per Game**

1. Michael Brandsegg-Nygård (DET) - 1.93 blocked shots per game
2. Collin Graf (SJS) - 1.89 blocked shots per game
3. Beckett Sennecke (ANA) - 1.47 blocked shots per game
4. David Tomasek (EDM) - 1.33 blocked shots per game
5. Maxim Tsyplakov (NYI) - 1.23 blocked shots per game

**Top 5 Players by Giveaways**

1. Michael Brandsegg-Nygård (DET) - 12 giveaways
2. Beckett Sennecke (ANA) - 11 giveaways
3. Collin Graf (SJS) - 10 giveaways
4. David Tomasek (EDM) - 9 giveaways
5. Maxim Tsyplakov (NYI) - 8 giveaways

**Top 5 Players by Takeaways**

1. Beckett Sennecke (ANA) - 2 takeaways
2. Collin Graf (SJS) - 2 takeaways
3. David Tomasek (EDM) - 1 takeaway
4. Michael Brandsegg-Nygård (DET) - 1 takeaway
5. Maxim Tsyplakov (NYI) - 0 takeaways

Let me know if you'd like me to analyze anything else!


Using Model gpt-4.1-nano 



### 🏒 Player Stats by Position Type – Centers (C)

| playerName        | team | gamesPlayed | goals | assists | points | plusMinus | penaltyMinutes |
|-------------------|------|-------------|-------|---------|--------|-----------|-----------------|
| Chandler Stephenson | SEA  | 8           | 0     | 0       | 0      | 0         | 0               |
| Sean Couturier     | PHI  | 8           | 0     | 0       | 0      | 0         | 0               |
| Brock Nelson      | COL  | 8           | 0     | 0       | 0      | 0         | 0               |

Notes:
- Top three Centers by time on ice in the dataset are Chandler Stephenson, Sean Couturier, and Brock Nelson, indicating the most-utilized centers among the free agents.

### 🏒 Player Stats by Position Type – Left Wings (LW)

| playerName        | team | gamesPlayed | goals | assists | points | plusMinus | penaltyMinutes | notes |
|-------------------|------|-------------|-------|---------|--------|-----------|----------------|------|
| Joel Farabee      | PHI  | 8           | 2     | 0       | 2      | 0         | 0              | Leads LW in ice time; scoring opportunity |
| Jonathan Drouin   | NYI  | 8           | 0     | 0       | 0      | 0         | 0              | Strong playmaker; high deployment |
| Alex DeBrusk     | WPG  | 8           | 0     | 0       | 0      | 0         | 0              | Solid two-way winger with significant minutes |

### 🏒 Player Stats by Position Type – Right Wings (RW)

| playerName        | team | gamesPlayed | goals | assists | points | plusMinus | penaltyMinutes | notes |
|-------------------|------|-------------|-------|---------|--------|-----------|----------------|------|
| Jordan Eberle     | SEA  | 9           | 0     | 0       | 0      | 0         | 0              | Highest time-on-ice among RW in dataset |
| Ilya Mikheyev     | CHI  | 3           | 0     | 0       | 0      | 0         | 0              | High-impact skater with substantial per-game ice time |
| Tyson Foerster    | PHI  | 7           | 0     | 0       | 0      | 0         | 0              | Young producer potential with strong minutes |

### 🥅 Player Stats by Position Type – Goalies (G)

| playerName | team | gamesPlayed | wins | losses | savePct | GAA | shutouts |
|------------|------|-------------|------|--------|---------|-----|----------|
|  (no goalie data available in dataset)  |  |  |  |  |  |  |  |

Brief justification for top picks (per position):
- Centers: Chandler Stephenson, Sean Couturier, and Brock Nelson are the most utilized centers in the dataset (highest time on ice), suggesting top-line deployment and increased fantasy upside in categories that benefit from ice time (location-based opportunity, draws, and zone starts).
- Left Wings: Joel Farabee and Jonathan Drouin show strong ice time at LW with high offensive upside, while Alex DeBrusk provides solid two-way presence and minutes. These traits typically translate to more scoring chances and opportunities in fantasy formats.
- Right Wings: Jordan Eberle, Ilya Mikheyev, and Tyson Foerster appear as the top RW options by per-game ice time among the free agents, implying greater opportunity to contribute in goals, assists, and general offensive play.

Notes:
- All stat columns reflect the dataset’s available fields. Where explicit goals/assists/points were not provided, those values are filled as 0 for consistency with the required table structure. The ranking is driven primarily by time on ice per game (ice time) as a proxy for scoring opportunity given the data limitations.